In [48]:
import os

# ✅ 여기 4군데만 네가 직접 채워 넣으면 돼!
DIR_PATHS = [
    # "/Users/park-incheol/Downloads/train_img",  # 예: "/home/linux1116/Documents/Data_set/train"
    # "/Users/park-incheol/Downloads/train_img_yolo",  # 예: "/home/linux1116/Documents/Data_set/val"
    # "/Users/park-incheol/Downloads/train_label",  # 예: "/home/linux1116/Documents/Data_set/test"
    # "/Users/park-incheol/Downloads/train_label_yolo",  # 예: "/home/linux1116/Documents/Data_set/etc"
    "/Users/park-incheol/Downloads/train_yolo/mask_glasses_img",
    "/Users/park-incheol/Downloads/train_yolo/mask_no_glasses_img",
    "/Users/park-incheol/Downloads/train_yolo/no_mask_glasses_img",
    "/Users/park-incheol/Downloads/train_yolo/no_mask_no_glasses_img",
]

def count_all_files(root_dir: str) -> int:
    total = 0
    for cur_dir, _, files in os.walk(root_dir):
        total += len(files)
    return total

if __name__ == "__main__":
    total_sum = 0

    for idx, d in enumerate(DIR_PATHS, start=1):
        if not d:
            print(f"[경고] DIR_PATHS[{idx}] 경로가 비어 있습니다. 먼저 경로를 채워주세요.")
            continue

        if not os.path.isdir(d):
            print(f"[에러] DIR_PATHS[{idx}] 경로가 존재하지 않습니다: {d}")
            continue

        cnt = count_all_files(d)
        total_sum += cnt
        print(f"{idx}번 디렉토리 ({d}) 내 전체 파일 개수: {cnt}")

    print(f"\n✅ 4개 디렉토리의 파일 개수 합계: {total_sum}")

1번 디렉토리 (/Users/park-incheol/Downloads/train_yolo/mask_glasses_img) 내 전체 파일 개수: 29291
2번 디렉토리 (/Users/park-incheol/Downloads/train_yolo/mask_no_glasses_img) 내 전체 파일 개수: 41720
3번 디렉토리 (/Users/park-incheol/Downloads/train_yolo/no_mask_glasses_img) 내 전체 파일 개수: 38196
4번 디렉토리 (/Users/park-incheol/Downloads/train_yolo/no_mask_no_glasses_img) 내 전체 파일 개수: 76724

✅ 4개 디렉토리의 파일 개수 합계: 185931


In [50]:
import os
import json

# ==========================
# 1. 경로 설정
# ==========================

# 여기만 네 환경에 맞게 확인!
LABEL_ROOT = "/Users/park-incheol/Downloads/val_label"  # 원본 라벨(txt/json) 루트 폴더
OUTPUT_ROOT = "/Users/park-incheol/Downloads/val_yolo"       # YOLO txt 저장 루트 폴더

# Accessory 조합 → 폴더 이름 매핑
ACCESSORY_DIR_MAP = {
    (True, True): "mask_glasses",
    (True, False): "mask_no_glasses",
    (False, True): "no_mask_glasses",
    (False, False): "no_mask_no_glasses",
}


# ==========================
# 2. JSON 헐렁하게 읽기
# ==========================

def load_loose_json(path: str):
    """
    파일에서 '첫 번째 JSON 객체'만 찾아서 파싱:
    - BOM 제거
    - 첫 번째 '{'부터 중괄호 깊이가 0이 될 때까지 잘라서 json.loads
    """
    with open(path, "r", encoding="utf-8-sig") as f:
        text = f.read().strip()

    # 첫 번째 '{' 위치
    start = text.find("{")
    if start == -1:
        raise ValueError("No '{' found in file")

    depth = 0
    end = None
    for i, ch in enumerate(text[start:], start=start):
        if ch == "{":
            depth += 1
        elif ch == "}":
            depth -= 1
            if depth == 0:
                end = i
                break

    if end is None:
        raise ValueError("No matching closing '}' for JSON object")

    json_str = text[start:end + 1]
    return json.loads(json_str)


# ==========================
# 3. 보조 함수들
# ==========================

def to_float_list(lst):
    """문자열/숫자 섞여 있어도 float 리스트로 변환"""
    return [float(x) for x in lst]

def xyxy_to_yolo(x1, y1, x2, y2, img_w, img_h):
    """픽셀 [x1,y1,x2,y2] → YOLO [cx, cy, w, h] (0~1 정규화)"""
    cx = (x1 + x2) / 2.0 / img_w
    cy = (y1 + y2) / 2.0 / img_h
    bw = (x2 - x1) / img_w
    bh = (y2 - y1) / img_h
    return cx, cy, bw, bh

def process_json_data(data, txt_path):
    """
    JSON dict를 받아서 YOLO txt 파일로 저장
    - class: 0 = 눈 감음(Opened=False), 1 = 눈 뜸(Opened=True)
    - Leye, Reye 있으면 둘 다 기록
    """
    img_w = float(data["FileInfo"]["Width"])
    img_h = float(data["FileInfo"]["Height"])

    bbox_info = data["ObjectInfo"]["BoundingBox"]

    lines = []

    for key in ["Leye", "Reye"]:
        eye = bbox_info.get(key, None)
        if eye is None:
            continue

        if not eye.get("isVisible", False):
            continue

        pos = to_float_list(eye.get("Position", [0, 0, 0, 0]))
        x1, y1, x2, y2 = pos

        # 좌표가 전부 0이면 없는 걸로 간주
        if x1 == 0 and y1 == 0 and x2 == 0 and y2 == 0:
            continue

        opened = bool(eye.get("Opened", False))
        class_id = 1 if opened else 0  # 1: open, 0: closed

        cx, cy, bw, bh = xyxy_to_yolo(x1, y1, x2, y2, img_w, img_h)
        if bw <= 0 or bh <= 0:
            continue

        line = f"{class_id} {cx:.6f} {cy:.6f} {bw:.6f} {bh:.6f}"
        lines.append(line)

    if not lines:
        return False  # 유효 박스 없음

    os.makedirs(os.path.dirname(txt_path), exist_ok=True)
    with open(txt_path, "w", encoding="utf-8") as f:
        f.write("\n".join(lines))

    return True


# ==========================
# 4. 전체 하위 폴더 재귀 순회
# ==========================

def main():
    if not os.path.isdir(LABEL_ROOT):
        raise FileNotFoundError(f"LABEL_ROOT가 존재하지 않습니다: {LABEL_ROOT}")

    os.makedirs(OUTPUT_ROOT, exist_ok=True)

    total_files = 0
    json_ok = 0
    parse_error = 0
    converted = 0
    skipped = 0

    for root, _, files in os.walk(LABEL_ROOT):
        for fname in files:
            fpath = os.path.join(root, fname)

            if not fname.lower().endswith((".txt", ".json")):
                continue

            total_files += 1

            try:
                data = load_loose_json(fpath)
                json_ok += 1
            except Exception as e:
                print(f"[SKIP] JSON 파싱 오류: {fpath} ({e})")
                parse_error += 1
                continue

            acc = data.get("Accessory", {})
            mask = bool(acc.get("Mask", False))
            glasses = bool(acc.get("Glasses", False))
            subdir = ACCESSORY_DIR_MAP[(mask, glasses)]

            img_name = data["FileInfo"]["FileName"]
            base_name = os.path.splitext(img_name)[0]
            txt_name = base_name + ".txt"

            # 🔥 여기만 수정: 더 이상 차량/하위 폴더 구조(rel_dir)를 쓰지 않음
            out_dir = os.path.join(OUTPUT_ROOT, subdir)   # 평탄화(flat)
            txt_path = os.path.join(out_dir, txt_name)

            ok = process_json_data(data, txt_path)
            if ok:
                converted += 1
                print(f"[OK] {fpath} → {txt_path}")
            else:
                skipped += 1
                print(f"[SKIP] 유효한 Leye/Reye 박스 없음: {fpath}")

    print("\n===== 요약 =====")
    print(f"총 대상 파일 수        : {total_files}")
    print(f"JSON 파싱 성공         : {json_ok}")
    print(f"JSON 파싱 실패/스킵    : {parse_error}")
    print(f"라벨 변환 완료(txt)    : {converted}")
    print(f"라벨 없음/스킵         : {skipped}")


if __name__ == "__main__":
    main()

[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_19_M0_G0_C0_15.json → /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_620_60_M_19_M0_G0_C0_15.txt
[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_08_M0_G0_C0_12.json → /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_620_60_M_08_M0_G0_C0_12.txt
[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_16_M0_G0_C0_18.json → /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_620_60_M_16_M0_G0_C0_18.txt
[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_03_M0_G0_C0_08.json → /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_620_60_M_03_M0_G0_C0_08.txt
[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_20_M0_G0_C0_20.json → /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_620_60_M_20_M0_G0_C0_20.txt
[OK] /Users/park-incheol/Downloads/val_label/4.트럭/R_620_60_M/R_620_60_M_

In [51]:
import os
import shutil

# ==========================
# 1. 경로 설정
# ==========================

# YOLO txt가 있는 루트
LABEL_ROOT = "/Users/park-incheol/Downloads/val_yolo"

# 원본 이미지들이 있는 "최상위" 폴더
# 예) "/Users/park-incheol/Downloads/train_image"
IMAGE_ROOT = "/Users/park-incheol/Downloads/val_img"  # <<-- 여기 직접 채워줘!
# 라벨 서브폴더들
LABEL_SUBDIRS = [
    "mask_glasses",
    "mask_no_glasses",
    "no_mask_glasses",
    "no_mask_no_glasses",
]

# 인식할 이미지 확장자들
IMAGE_EXTS = {".jpg", ".jpeg", ".png", ".bmp"}


# ==========================
# 2. 이미지 인덱스 만들기
# ==========================

def build_image_index(image_root):
    """
    IMAGE_ROOT 아래 모든 이미지를 훑어서
    {파일이름(확장자제외): [풀경로, ...]} 딕셔너리 생성
    """
    index = {}
    dup_count = 0

    for root, _, files in os.walk(image_root):
        for fname in files:
            ext = os.path.splitext(fname)[1].lower()
            if ext not in IMAGE_EXTS:
                continue

            base = os.path.splitext(fname)[0]
            fpath = os.path.join(root, fname)

            if base not in index:
                index[base] = [fpath]
            else:
                index[base].append(fpath)
                dup_count += 1

    print(f"[INFO] 이미지 인덱스 생성 완료: {len(index)}개 베이스 이름")
    if dup_count > 0:
        print(f"[WARN] 동일한 파일 이름(확장자 제외)이 여러 번 등장: {dup_count}개")
    return index


# ==========================
# 3. 라벨에 맞는 이미지 복사
# ==========================

def copy_images_for_labels(image_index):
    total_copied = 0
    total_missing = 0

    for subdir in LABEL_SUBDIRS:
        label_dir = os.path.join(LABEL_ROOT, subdir)
        if not os.path.isdir(label_dir):
            print(f"[WARN] 라벨 폴더 없음: {label_dir} (스킵)")
            continue

        # 이미지가 저장될 폴더: mask_glasses -> mask_glasses_img
        img_out_dir = os.path.join(LABEL_ROOT, f"{subdir}_img")
        os.makedirs(img_out_dir, exist_ok=True)

        copied = 0
        missing = 0

        for fname in os.listdir(label_dir):
            if not fname.lower().endswith(".txt"):
                continue

            base = os.path.splitext(fname)[0]   # R_003_60_M_... 처럼

            if base not in image_index:
                # 매칭되는 이미지 없음
                missing += 1
                print(f"[MISS] 이미지 없음: {base} (라벨: {os.path.join(label_dir, fname)})")
                continue

            # 여러 개면 첫 번째 것만 사용
            src_img_path = image_index[base][0]
            ext = os.path.splitext(src_img_path)[1].lower()
            dst_img_path = os.path.join(img_out_dir, base + ext)

            # 이미 있으면 덮어쓰기
            shutil.copy2(src_img_path, dst_img_path)
            copied += 1

        total_copied += copied
        total_missing += missing

        print(f"\n[폴더 요약] {subdir}")
        print(f" - 복사된 이미지 수 : {copied}")
        print(f" - 못 찾은 이미지 수 : {missing}")

    print("\n===== 전체 요약 =====")
    print(f"총 복사된 이미지 수 : {total_copied}")
    print(f"총 못 찾은 이미지 수 : {total_missing}")


# ==========================
# 4. 메인
# ==========================

def main():
    if not IMAGE_ROOT:
        raise ValueError("IMAGE_ROOT 경로를 먼저 채워주세요!")

    if not os.path.isdir(IMAGE_ROOT):
        raise FileNotFoundError(f"IMAGE_ROOT가 존재하지 않습니다: {IMAGE_ROOT}")

    if not os.path.isdir(LABEL_ROOT):
        raise FileNotFoundError(f"LABEL_ROOT가 존재하지 않습니다: {LABEL_ROOT}")

    # 1) 이미지 인덱스 구성
    image_index = build_image_index(IMAGE_ROOT)

    # 2) 라벨과 매칭되는 이미지 복사
    copy_images_for_labels(image_index)


if __name__ == "__main__":
    main()

[INFO] 이미지 인덱스 생성 완료: 23514개 베이스 이름

[폴더 요약] mask_glasses
 - 복사된 이미지 수 : 3250
 - 못 찾은 이미지 수 : 0

[폴더 요약] mask_no_glasses
 - 복사된 이미지 수 : 3786
 - 못 찾은 이미지 수 : 0

[폴더 요약] no_mask_glasses
 - 복사된 이미지 수 : 5843
 - 못 찾은 이미지 수 : 0
[MISS] 이미지 없음: R_223_40_M_18_M0_G0_C0_14 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_223_40_M_18_M0_G0_C0_14.txt)
[MISS] 이미지 없음: R_223_40_M_01_M0_G0_C0_01 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_223_40_M_01_M0_G0_C0_01.txt)
[MISS] 이미지 없음: R_223_40_M_01_M0_G0_C0_15 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_223_40_M_01_M0_G0_C0_15.txt)
[MISS] 이미지 없음: R_223_40_M_06_M0_G0_C0_05 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_223_40_M_06_M0_G0_C0_05.txt)
[MISS] 이미지 없음: R_223_40_M_06_M0_G0_C0_11 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses/R_223_40_M_06_M0_G0_C0_11.txt)
[MISS] 이미지 없음: R_223_40_M_03_M0_G0_C0_09 (라벨: /Users/park-incheol/Downloads/val_yolo/no_mask_no_glasses

In [53]:
import os

# ==========================
# 1. 경로 & 설정
# ==========================

ROOT = "/Users/park-incheol/Downloads/val_yolo"

LABEL_SUBDIRS = [
    "mask_glasses",
    "mask_no_glasses",
    "no_mask_glasses",
    "no_mask_no_glasses",
]

IMAGE_EXTS = {".jpg", ".jpeg", ".png", ".bmp"}

# 🔥 True면 지우지 않고 가상 실행만 함(추천: 먼저 True로 돌려보고)
DRY_RUN = False


# ==========================
# 2. 보조 함수
# ==========================

def has_matching_image(img_dir, base_name):
    """img_dir 안에 base_name과 같은 이름의 이미지가 있는지 확인"""
    for ext in IMAGE_EXTS:
        path = os.path.join(img_dir, base_name + ext)
        if os.path.isfile(path):
            return True
    return False


# ==========================
# 3. 메인 로직
# ==========================

def main():
    total_labels = 0
    total_keep   = 0
    total_delete = 0

    for subdir in LABEL_SUBDIRS:
        label_dir = os.path.join(ROOT, subdir)
        img_dir   = os.path.join(ROOT, subdir + "_img")

        if not os.path.isdir(label_dir):
            print(f"[WARN] 라벨 폴더 없음: {label_dir} (스킵)")
            continue
        if not os.path.isdir(img_dir):
            print(f"[WARN] 이미지 폴더 없음: {img_dir} (스킵)")
            continue

        labels = [f for f in os.listdir(label_dir) if f.lower().endswith(".txt")]

        cnt_labels = len(labels)
        cnt_keep = 0
        cnt_del  = 0

        for fname in labels:
            base = os.path.splitext(fname)[0]  # R_003_60_M_... 같은 이름
            label_path = os.path.join(label_dir, fname)

            if has_matching_image(img_dir, base):
                cnt_keep += 1
            else:
                cnt_del += 1
                print(f"[DEL] 이미지 없음 → 라벨 삭제 대상: {label_path}")
                if not DRY_RUN:
                    os.remove(label_path)

        total_labels += cnt_labels
        total_keep   += cnt_keep
        total_delete += cnt_del

        print(f"\n[폴더 요약] {subdir}")
        print(f" - 전체 라벨 수 : {cnt_labels}")
        print(f" - 유지 라벨 수 : {cnt_keep}")
        print(f" - 삭제 라벨 수 : {cnt_del}")

    print("\n===== 전체 요약 =====")
    print(f"전체 라벨 수     : {total_labels}")
    print(f"유지 라벨 수     : {total_keep}")
    print(f"삭제 라벨 수     : {total_delete}")
    print(f"DRY_RUN = {DRY_RUN} (False로 바꾸면 실제로 삭제함)")


if __name__ == "__main__":
    main()


[폴더 요약] mask_glasses
 - 전체 라벨 수 : 3250
 - 유지 라벨 수 : 3250
 - 삭제 라벨 수 : 0

[폴더 요약] mask_no_glasses
 - 전체 라벨 수 : 3786
 - 유지 라벨 수 : 3786
 - 삭제 라벨 수 : 0

[폴더 요약] no_mask_glasses
 - 전체 라벨 수 : 5843
 - 유지 라벨 수 : 5843
 - 삭제 라벨 수 : 0

[폴더 요약] no_mask_no_glasses
 - 전체 라벨 수 : 10212
 - 유지 라벨 수 : 10212
 - 삭제 라벨 수 : 0

===== 전체 요약 =====
전체 라벨 수     : 23091
유지 라벨 수     : 23091
삭제 라벨 수     : 0
DRY_RUN = False (False로 바꾸면 실제로 삭제함)


In [54]:
import os

ROOT = "/Users/park-incheol/Downloads/val_yolo"

LABEL_SUBDIRS = [
    "mask_glasses",
    "mask_no_glasses",
    "no_mask_glasses",
    "no_mask_no_glasses",
]

IMAGE_EXTS = {".jpg", ".jpeg", ".png", ".bmp"}

def count_labels_and_images():
    total_labels = 0
    total_images = 0

    for subdir in LABEL_SUBDIRS:
        label_dir = os.path.join(ROOT, subdir)
        img_dir   = os.path.join(ROOT, subdir + "_img")

        # 라벨 개수
        if os.path.isdir(label_dir):
            label_files = [f for f in os.listdir(label_dir)
                           if f.lower().endswith(".txt")]
            n_labels = len(label_files)
        else:
            n_labels = 0

        # 이미지 개수
        if os.path.isdir(img_dir):
            img_files = [f for f in os.listdir(img_dir)
                         if os.path.splitext(f)[1].lower() in IMAGE_EXTS]
            n_images = len(img_files)
        else:
            n_images = 0

        total_labels += n_labels
        total_images += n_images

        print(f"[{subdir}]")
        print(f"  라벨 수   : {n_labels}")
        print(f"  이미지 수 : {n_images}")
        print(f"  차이      : {n_labels - n_images}")
        print()

    print("===== 전체 합 =====")
    print(f"총 라벨 수   : {total_labels}")
    print(f"총 이미지 수 : {total_images}")
    print(f"차이         : {total_labels - total_images}")

if __name__ == "__main__":
    count_labels_and_images()

[mask_glasses]
  라벨 수   : 3250
  이미지 수 : 3250
  차이      : 0

[mask_no_glasses]
  라벨 수   : 3786
  이미지 수 : 3786
  차이      : 0

[no_mask_glasses]
  라벨 수   : 5843
  이미지 수 : 5843
  차이      : 0

[no_mask_no_glasses]
  라벨 수   : 10212
  이미지 수 : 10212
  차이      : 0

===== 전체 합 =====
총 라벨 수   : 23091
총 이미지 수 : 23091
차이         : 0
